In [1]:
# install all these packages once
'''
!pip install --upgrade pip
!pip install git+https://github.com/openai/whisper.git 
!pip install pytube==12.1.0
!pip install pydub==0.25.1

!pip install -q transformers==4.24.0

!pip install sentencepiece==0.1.97
!pip install git+https://github.com/csebuetnlp/normalizer

# !pip install ffmpeg==1.4
!pip install ffmpeg-python==0.2.0

#! pip install -U pip
! pip install TTS==0.8.0
! pip install bnnumerizer==0.0.2
! pip install bangla==0.0.2
! pip install gdown==4.5.1
! pip install bnunicodenormalizer==0.1.1
! pip install PyArabic==0.6.15
#! pip install pydub
! pip install Unidecode==1.3.6
#! pip install numpy
!pip install pydload==1.0.9

!pip install mishkal
!pip install codernitydb3
''' 

!nvidia-smi

Fri Nov 11 11:38:49 2022       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 515.65.01    Driver Version: 515.65.01    CUDA Version: 11.7     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  NVIDIA RTX A6000    Off  | 00000000:65:00.0 Off |                  Off |
| 30%   33C    P8    28W / 300W |   3551MiB / 49140MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [2]:
!pwd

/home/ansary/Shabab/Multilingual_speech_to_speech


In [3]:
# ...................CONTROLS.................

make_youtube_audio_playlist = False

run_multilingual_stt = False

run_en_ar_bn_translator = False

run_multilingual_tts = True

In [4]:
import os
import soundfile as sf
import torch
import transformers
from IPython.display import Audio
print(transformers.__version__)
print(torch.__version__)

4.24.0
1.12.1


/home/ansary/anaconda3/envs/mobassir/lib/python3.8/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [5]:
%%time
if(make_youtube_audio_playlist):
    !python -W ignore step1_make_youtube_audio_playlist.py


#https://towardsdatascience.com/speech-to-text-with-openais-whisper-53d5cea9005e
# import pytube
# # Reading from Youtube video link
# video = 'https://www.youtube.com/watch?v=dP--QLPUK_8'
# data = pytube.YouTube(video)
# # Converting and downloading as 'MP4' file
# audio = data.streams.get_audio_only()
# audio.download()

# !ffmpeg -i '/home/apsisdev/mobassir/data/Multilingual-Speech-to-Speech-Translator-main/Seerah_of_Prophet_Muhammed_SAW/Seerah of Prophet Muhammad 84 - Conversion of Kab ibn Zuhayr  Dr Yasir Qadhi  7th May 2014.mp4' -ac 2 -f wav '/home/apsisdev/mobassir/data/Multilingual-Speech-to-Speech-Translator-main/Seerah_of_Prophet_Muhammed_SAW/84.Seerah_of_Prophet_Muhammad_84_Conversion_of_Kab_ibn_Zuhayr_Dr_Yasir_Qadhi_7th_May_2014.wav'

CPU times: user 1e+03 ns, sys: 2 µs, total: 3 µs
Wall time: 4.29 µs


In [6]:
!ls

 bangla_tts
'E2E-Multilingual Speech to Speech Translator.ipynb'
 E2E_Single_Sample_Demo_of_Multilingual_Speech_to_Speech_Translation.ipynb
 e2e_single_sample_demo_of_multilingual_speech_to_speech_translation.py
 empty.wav
 klaam
 LICENSE
 model.pth.tar
 __pycache__
 README.md
 step1_make_youtube_audio_playlist.py
 step2_run_multilingual_stt.py
 step3_crosslingual_translator.py
 step4_multilingual_tts.py
 yasir_qadhi_seerah
 youtube-playlist-downloader.ipynb


In [7]:
#!ls Seerah_of_Prophet_Muhammed_SAW


In [8]:
%%time
if(run_multilingual_stt):
    from step2_run_multilingual_stt import mlt_speech_to_text_convertor
    folder_path = os.path.join(os.getcwd() , 'Seerah_of_Prophet_Muhammed_SAW') 
    
    files = sorted(os.listdir(folder_path))
    for i in range(len(files)):
        TEXTS = ''
        try:
            TEXTS = mlt_speech_to_text_convertor(path = files[i],silence_based_conversion = False)
        except:
            print("couldn't make -> ".i)

        mlt_txt = ' '.join(TEXTS)

        head, output = os.path.split(files[i])
        fname = output.split(".")[1]

        path = "mlt_stt_outputs"
        isExist = os.path.exists(path)
        if not isExist:
            os.makedirs(path)
        os.chdir(path)

        text_file = open(f"en_{fname}.txt", "w")
        n = text_file.write(mlt_txt)
        text_file.close()
        os.chdir('..')

CPU times: user 1e+03 ns, sys: 2 µs, total: 3 µs
Wall time: 7.63 µs


In [9]:
pwd

'/home/ansary/Shabab/Multilingual_speech_to_speech'

In [10]:
%%time

if(run_en_ar_bn_translator):
    from step3_crosslingual_translator import EN_AR_to_BN_AR_Translator
    folder_path = os.path.join(os.getcwd() , 'mlt_stt_outputs') 
    files = sorted(os.listdir(folder_path))
    path = "bn_translated_outputs"
    isExist = os.path.exists(path)
    if not isExist:
        os.makedirs(path)

    for i in range(len(files)):
        fpath = os.path.join(folder_path , files[i]) 
        f = open(f"{fpath}", "r")
        fread = f.read()
        try:
            bn_mlt = EN_AR_to_BN_AR_Translator(fread,tag_text = True)
        except:
            print("couldn't process -> ",i," filename -> ",files[i])
        # bn_mlt=bn_mlt.replace("</ar>",' ')
        # bn_mlt=bn_mlt.replace("<ar>",' ')

        fname = files[i]
        fname = fname.replace("en",'bn')
        fname = fname.split(".")[0]
        
        os.chdir(path)

        text_file = open(f"{fname}.txt", "w")
        n = text_file.write(bn_mlt)
        text_file.close()
        os.chdir('..')
        

CPU times: user 1 µs, sys: 2 µs, total: 3 µs
Wall time: 4.29 µs


In [11]:
%%time

if(run_multilingual_tts):
    !git clone https://github.com/ARBML/klaam
    # make sure you have these installed https://github.com/ARBML/klaam/blob/main/requirements.txt
    from step4_multilingual_tts import BigTextToAudio
    
    folder_path = os.path.join(os.getcwd() , 'yasir_qadhi_seerah/y.q_bn_seerah') 
    files = sorted(os.listdir(folder_path))
    path = "bangla_seerah"
    isExist = os.path.exists(path)
    if not isExist:
        os.makedirs(path)

    for i in range(len(files)):
        fpath = os.path.join(folder_path , files[i]) 
        f = open(f"{fpath}", "r")
        fread = f.read()
        MLT_TTS=BigTextToAudio()
        fname = files[i]
#         fname = fname.replace("en",'bn')
        fname = fname.split(".")[0]
        try:
            audio=MLT_TTS(fread,resample_audio_to_out_sample_rate=False)
            sf.write(f'bangla_seerah/{fname}.wav', audio, 22050)
#             os.chdir(path)
            print(f"File {i} processing done!")
        except:
            print("couldn't process -> ",i," filename -> ",files[i])

#         os.chdir('..')
    



fatal: destination path 'klaam' already exists and is not an empty directory.
Removing weight norm...
 > Using model: vits
 > Setting up Audio Processor...
 | > sample_rate:22050
 | > resample:False
 | > num_mels:80
 | > log_func:np.log10
 | > min_level_db:0
 | > frame_shift_ms:None
 | > frame_length_ms:None
 | > ref_level_db:None
 | > fft_size:1024
 | > power:None
 | > preemphasis:0.0
 | > griffin_lim_iters:None
 | > signal_norm:None
 | > symmetric_norm:None
 | > mel_fmin:0
 | > mel_fmax:None
 | > pitch_fmin:None
 | > pitch_fmax:None
 | > spec_gain:20.0
 | > stft_pad_mode:reflect
 | > max_norm:1.0
 | > clip_norm:True
 | > do_trim_silence:False
 | > trim_db:60
 | > do_sound_norm:False
 | > do_amp_to_db_linear:True
 | > do_amp_to_db_mel:True
 | > do_rms_norm:False
 | > db_level:None
 | > stats_path:None
 | > base:10
 | > hop_length:256
 | > win_length:1024
couldn't numerize bengali.
skipped
['m', 'H', 'm', 'd']
skipped
['uu0', 'E', 'l', 'aa']
skipped
['UU0', 'S', 'H', 'b', 'h']
skipped


skipped
['l', 'l', 'h']
Raw Text Sequence: حسبنا كتاب الله
Phoneme Sequence: {H s b n aa k t aa b l l h sil}
['<BLNK>', 'ক', '<BLNK>', 'ি', '<BLNK>', 'ন', '<BLNK>', '্', '<BLNK>', 'ত', '<BLNK>', 'ু', '<BLNK>', ' ', '<BLNK>', 'আ', '<BLNK>', 'ম', '<BLNK>', 'া', '<BLNK>', 'দ', '<BLNK>', 'ে', '<BLNK>', 'র', '<BLNK>', ' ', '<BLNK>', 'ব', '<BLNK>', 'ই', '<BLNK>', '<', '<BLNK>', '>', '<BLNK>', '।', '<BLNK>']
 [!] Character '<' not found in the vocabulary. Discarding it.
['<BLNK>', 'ক', '<BLNK>', 'ি', '<BLNK>', 'ন', '<BLNK>', '্', '<BLNK>', 'ত', '<BLNK>', 'ু', '<BLNK>', ' ', '<BLNK>', 'আ', '<BLNK>', 'ম', '<BLNK>', 'া', '<BLNK>', 'দ', '<BLNK>', 'ে', '<BLNK>', 'র', '<BLNK>', ' ', '<BLNK>', 'ব', '<BLNK>', 'ই', '<BLNK>', '<', '<BLNK>', '>', '<BLNK>', '।', '<BLNK>']
 [!] Character '>' not found in the vocabulary. Discarding it.
--------------------->>>>>>>>>>>>>>>>>>>>>>>>>>>    failed ar => এটা না  end
--------------------->>>>>>>>>>>>>>>>>>>>>>>>>>>    failed ar =>  আমরা জানি না কে বলেছে এটা আর অ

Raw Text Sequence: ثاني اثنين
Phoneme Sequence: {^ aa n ii0 ^ n ii0 n sil}
skipped
['m', 'n']
Raw Text Sequence: والسابقون الأولون من المهاجرين والأنصار والذين تبعوهم بإحسان
Phoneme Sequence: {w a l s aa b q uu0 n l < uu0 l uu0 n m n l m h aa j r ii0 n w a l < n S AA r w a l * ii0 n t b E uu0 h m b < i0 H s aa n sil}
Raw Text Sequence: السابقون الأولون
Phoneme Sequence: {< a l s aa b q uu0 n l < uu0 l uu0 n sil}
skipped
['l', 'm']
skipped
['ii0', 'k', 'n']
Raw Text Sequence: لم يكن سهلا لماذا
Phoneme Sequence: {l m ii0 k n s h l aa l m aa * aa sil}
--------------------->>>>>>>>>>>>>>>>>>>>>>>>>>>    failed ar =>  ليس خطأ أبو بكر أشياء تحدث في خلافته لم تكن سهلا لأن ماذا حدث في خلافته  end
--------------------->>>>>>>>>>>>>>>>>>>>>>>>>>>    failed ar =>  حروب الرده جميع الأمة تشدد الأمة كانت قادمة على التسقط وقام الله بإنقاذها عبر أبو بكر لذا لم يكن سهلا ليس أن أبو بكر مشكلة هناك أشياء تحدث  end
skipped
['k', '<', 'l', 'm']
skipped
['t', 'g', 'n', 'b']
skipped
['l', 'm', 's']
Raw Text S

skipped
['l', 'E', 'r', 'b']
skipped
['ii0', 's', 'm', 'aa']
skipped
['m', 'x', 'z', 'n']
skipped
['f', 'q', 'T']
skipped
['ii0', 'g', 'T', 'ii0']
skipped
['l', 'm', 'x', 'z', 'n']
skipped
['m', 'x', 'z', 'n']
skipped
['l', 'm', 'x', 'z', 'n']
skipped
['ii0', 't', 'E', 'ii0', '$']
skipped
['m', 'n']
skipped
['ii0', 't', 'E', 'ii0', '$']
skipped
['b', 'n']
skipped
['l', 'm', 's', 't', 'm', 'r']
skipped
['m', 'n']
skipped
['m', 'n']
skipped
['q', 'b', 'l']
skipped
['k', 't', 'b']
skipped
['l', 'E', 'r', 'b']
Raw Text Sequence: وهذا في العرب يسمى سقيفة سقيفة هو مغطى أو مخزن شيء فقط يغطي و هذا المخزن أو هذا سقيفة كان في مخزن و المخزن يتعيش بالمعروفين من خزرانيين والذين هو بني ساعدة والذين هو ما يتعيش ساعد بن عبادة وهذا كان المكان المستمر في المجموعة من أجل الجاهلية من قبل الإسلام كان لديهم مجموعة تقريبا كانت كتب العرب
Phoneme Sequence: {w a h aa * aa f ii0 l E r b ii0 s m aa s q ii0 f s q ii0 f h uu0 m g T AA < a w m x z n $ ii0 < f q T ii0 g T ii0 w a h aa * aa l m x z n < a w h aa * aa s

skipped
['H', 'd', '^']
skipped
['l', 'b', 'n']
skipped
['H', 'd', '^']
skipped
['m', 'n']
skipped
['b', 'n']
skipped
['b', 'E', 'D']
skipped
['m', 'S', 'r']
skipped
['b', 'n']
skipped
['l', 'l', 'h']
skipped
['l', 'f', 'r', 'S']
skipped
['E', 'n']
skipped
['x', 'm', 'r']
skipped
['<', 'A', 'S', 'b', 'H', 't']
skipped
['m', 'H', 'r', 'r']
skipped
['m', 'S', 'r']
skipped
['b', 'n']
skipped
['l', 'b', 'n']
skipped
['H', 'd', '^']
skipped
['<', 'A', 'S', 'b', 'H', 't']
skipped
['m', 'S', 'r']
skipped
['b', 'n']
skipped
['<', 'A', 'S', 'b', 'H', 't']
skipped
['l', 'b', 'q', 'r']
skipped
['l', 'l', 'h']
skipped
['uu0', 't', 'E', 'aa', 'l', 'aa']
skipped
['II0', 'q', 'uu0', 'l']
skipped
['l', 'b', 'q', 'r']
Raw Text Sequence: ما حدث في هذا الوقت ليس مرتبطا لبن نظير لكنه حدث في الوقت من بن نظير بعض المعلومات تقول أنه عندما كانت المسلمين مرتبطا خارج مصر بن نظير الله أخبرنا الفرصة الأخيرة عن الكحول أي خمر أصبحت محرر في مصر بن نظير الآن ليس مرتبطا لبن نظير لكنه حدث أن هذا هو الوقت الذي أصبحت عند

...

skipped
['uu0', 'E', 'm', 'n', 'uu0']
Raw Text Sequence: إن الذين آمنوا وعمنوا الصالحات
Phoneme Sequence: {< i0 n l * ii0 n < aa m n uu0 uu0 E m n uu0 l S AA l H aa t sil}
skipped
['l', 'H', 'q']
skipped
['s', 't', '*', 'h', 'b']
skipped
['l', 'j', 'n']
skipped
['s', 't', '*', 'h', 'b']
skipped
['m', 'n']
skipped
['$', 'x', 'S']
skipped
['l', 'l', 'h']
skipped
['q', 'l', 't', 'h']
skipped
['l', '*', 'l', 'k']
skipped
['b', 'k', 'r']
skipped
['s', 'ii0', '*', 'h', 'b']
skipped
['l', 'j', 'n']
skipped
['s', 'ii0', '*', 'h', 'b']
skipped
['l', '<', 'n']
skipped
['l', 'l', 'h']
skipped
['E', 'm', 'r']
skipped
['s', 'ii0', '*', 'h', 'b']
skipped
['l', 'j', 'n']
skipped
['s', 'ii0', '*', 'h', 'b']
skipped
['l', '<', 'n']
skipped
['l', 'l', 'h']
skipped
['m', 'n']
skipped
['$', 'x', 'S']
skipped
['m', 'n']
skipped
['<', 'a', 'f', 'D', 'l']
skipped
['<', 'a', 'n', 'h', 'm']
skipped
['l', 'j', 'n']
Raw Text Sequence: لدينا الحق في قول أنك ستذهب إلى الجنة و ستذهب إلى الجحيم لا لا تقول هذا من أي 

skipped
['m', 'j', 'r', 'd']
skipped
['r', 'j', 'l']
skipped
['m', 'H', 't', 'r', 'm']
skipped
['l', 'm']
skipped
['II0', 'q', 'r', 'r']
skipped
['b', '<', 'n']
skipped
['II0', 'q', 'uu0', 'l']
skipped
['n', 'E', 'm']
skipped
['l', 'q', 'd']
skipped
['H', 'S', 'l']
skipped
['l', 'm']
skipped
['ii0', 'H', 't', 'aa', 'j']
skipped
['m', 'j', 'r', 'd']
skipped
['r', 'j', 'l']
skipped
['m', 'H', 't', 'r', 'm']
skipped
['uu0', 'm', 't', 'n', 'b', 'h', 'r']
skipped
['ii0', 'H', 't', 'aa', 'j']
skipped
['ii0', 's', '<', 'l']
skipped
['H', 'S', 'l']
skipped
['m', 'n']
skipped
['UU0', 'q', 'AA', 'l']
Raw Text Sequence: كان مجرد رجل محترم جدا لم يقرر بأن يقول نعم لقد حصل على المساعدة حتى لو لم يحتاج إلى المساعدة إنه مجرد رجل محترم ومتنبهر لا يحتاج إلى أن يسأل أبي لكنه حصل على المساعدة من أبي وقال أبي ما رأيك
Phoneme Sequence: {k aa n m j r d r j l m H t r m j d aa l m II0 q r r b < n II0 q uu0 l n E m l q d H S l E l aa l m s aa E d H t aa l uu0 l m ii0 H t aa j < i0 l aa l m s aa E d < i0 n h m 

--------------------->>>>>>>>>>>>>>>>>>>>>>>>>>>    failed ar =>  لا أقول ذلك ، وقد سمعت الكثير من الناس عندما يحدث شيء جيد ، سيقولون جزاك الله الله لا تقول جزاك الله الله جزاك الله يأتي لك أنت لا ترسل الجزاء إلى الله إنه خطأ كبير حتى لو أنهم يفعلونه بشكل غير مجاني أنت لا ترسل الجزاء إلى الله أنت لا ترسل السلام إلى الله لا تقول وعليك السلام يا الله الله هو السلام هذا هو رسالة خديج وعلى جبريل السلام وعليك يا رسول الله السلام وعليك يا رسول الله السلام هذا كان رسالة خديجة وعائشة التي كانت بالتأكيد زوجة أفضل من نبيه السلام في فئة مدينة بالطبع في هذه الفئة عائشة لم تنبأ حتى الآن عندما  end
Raw Text Sequence: لماذا
Phoneme Sequence: {l m aa * aa sil}
--------------------->>>>>>>>>>>>>>>>>>>>>>>>>>>    failed ar =>  لحب رسول الله صلى الله عليه وسلم لها لأنني كنت أعرف كم أحبها رسول الله صلى الله عليه وسلم كانت عزيزة جدا كم أحبها رسول الله صلى الله عليه وسلم كنت أعرفها لذا كنت أغرق أكثر من خديجة وعندما كان رسول الله صلى الله عليه وسلم يذكر خديجة قالت لقد كانت لديها كافة كانت ذلك وقلت يا رسول ال

skipped
['m', 'k']
skipped
['m', 'H', 'l']
skipped
['m', 'n']
skipped
['uu0', 'm', 'r']
Raw Text Sequence: مكة في محل العديد من الجبال ومرة واحدة في
Phoneme Sequence: {m k f ii0 m H l l E d ii0 d m n l j b aa l uu0 m r w aa H d f ii0 sil}
skipped
['<', 'a', 'k', '^', 'r']
skipped
['m', 'H', 'l']
skipped
['l', 'q', 'd']
skipped
['m', 'n']
skipped
['l', 'H', 'j', 'z']
skipped
['q', 'm', 't']
skipped
['b', 'h']
skipped
['ii0', 'm', 'k', 'n', 'n', 'ii0']
skipped
['k', 'n', 't']
skipped
['UU0', 'q', 'd']
skipped
['q', 'm', 't']
skipped
['l', 'H', 'j', 'z']
skipped
['<', 'A', 'q', 's', 'm']
skipped
['k', 'n', 't']
skipped
['<', 'a', 't', 's', 'l', 'q']
skipped
['m', 'n']
skipped
['l', 'k', 'E', 'b']
skipped
['l', '<', 'n']
skipped
['<', 'A', 'q', 's', 'm']
skipped
['b', '<', 'n']
skipped
['l', '<', 'n']
skipped
['m', 'k']
Raw Text Sequence: سنوات أو أكثر هناك محل عظيم لقد رأيت هذا نفسي في واحد من الحجز الذي قمت به لا يمكنني رؤية هذا بالكاد كنت أرى هذا وقد قمت بهذا الحجز في هذا العام أقسم بأن

skipped
['ii0', 's', 't', 'x', 'd', 'm', 'uu0', 'n']
skipped
['l', 'm', 'E', 'j', 'z']
skipped
['ii0', '<', 't', 'ii0']
skipped
['l', 'm', 'E', 'j', 'z']
skipped
['m', 'S', 'd', 'r']
skipped
['l', '*', 'l', 'k']
skipped
['b', '<', 'n', 'h', 'm']
skipped
['l', 'm']
skipped
['ii0', 's', 't', 'T', 'E', 'uu0']
skipped
['m', 'j', 'r', 'd']
skipped
['UU0', 'q', 't']
skipped
['l', '*', 'l', 'k']
skipped
['l', 'm', 'j', 'r', 'd']
Raw Text Sequence: كانوا يستخدمون الأشياء المعجزة لتصميم الأساس لكي عندما يأتي المعجزة القادمة ستكون مصدر صالح لذلك قموا بالتحقيق بأنهم لم يستطعوا تبني الأساس كما كانت الأساس الأولى كانت الأساس الأولى ليست كائنة كانت مجرد مبنى كانت الأساس الأولى في وقت إبراهيم عليه السلام كانت مبنى لذلك المجرد والأعلى
Phoneme Sequence: {k aa n uu0 ii0 s t x d m uu0 n l < $ y aa < l m E j z l t S m ii0 m l < s aa s l k ii0 E n d m aa ii0 < t ii0 l m E j z l q AA d m s t k uu0 n m S d r S AA l H l * l k q m uu0 b aa l t H q II0 q b < n h m l m ii0 s t T E uu0 t b n ii0 l < s aa s k m aa

In [12]:
# text = '''<ar>بكت عيني بكت عيني بكت عيني على ذنبي وما لاقيت من كربي</ar> and do not fear from the punishment. will be the hafidh of the Quran the martyr the Shaheed and The one who gave of his money all the time for the sake of Allah these are the first three people whom Allah will call in front of him and As everybody is looking at them, they will think Allah is honoring them Allah is rewarding them Allah will give them the first share of the pie of Jannah gatherings and at these masajid. Why did you go and do this? So the hafidh will stand up with pride and he will say, Oh Allah, I did it to bring honor to your book. I did it for the izzah of the religion, for the glory of the religion. I did it for your sake, Oh Allah. And Allah will say, You're lying. And the angels will agree and say, You are lying. And the books will be barred forth and it will be clear that his intention, Allah will say, your intention was not to please me. the Quran so that people would call you Qari, Hafiz, Sheikh and they did. So get your reward from them. And then the second person, the martyr, the one who waged a legitimate expedition and he gave his life for the cause of Allah subhanahu wa ta'ala. He will be asked why did you spend your life in the way of Allah and the man will say because I wanted to bring help to the religion. I wanted to defend the religion, defend the weakless and the homeless and the poor. I did it for your sake, O Allah. And Allah will once again say, <ar>كذبت</ar>, you're lying. And the angels will testify you're lying. And Allah will say, you only did it so that people could call you, mashaAllah, Mujahid, mashaAllah, brave man, mashaAllah, you've done so much. And the people did. You got your reward from them, none from Me. And the same with the third person, and for your religion. And Allah will say you only did it so that you could be known in the community. So that people would call you generous and that is exactly what they did. And then Allah will punish these three in front of all of the creation and they will be the very first people to enter the fire of hell. Wa liyadubillah. And Abu Huraira was listening to this hadith and the Prophet tapped his knee and he said, Ya Aba Huraira, these are the first three people the Hafidh and Qari and in one rewired says the scholar and the orator may Allah azza wa jalla protect all of us and The one who was a Shaheed the martyr and the third one is the one who is generous why? Because their intentions were not correct. They had this mixing of intentions They wanted to show off their deeds and imagine brothers and sisters Imagine the fate of the person he's doing good his whole life and he thinks he's gonna meet Allah with all of this good and then he is told, you didn't do it for my sake. You did it for your own ego. You did it to inflate your own prestige on the people. Why are you wanting me to reward you when you didn't do it purely for my sake? Imagine the fate of that person and therefore brothers and sisters, we need to make sure we are not that person. We are not that person on the day of judgment who is told you wasted your whole life and all of your deeds will be thrown back at your face. <ar>اخلي ويا خجلي اذا ما قال لي ربي اما استحييته تعصيني ولا تخشى من العتبي وتخفي الذنب عن خلقي وتأبى في الهوى قربي تعود إلى رضا ربي</ar>'''

In [13]:
# text = text.replace("<ar>"," ")
# text = text.replace("</ar>"," ")
# text

In [14]:

# Audio(audio, rate=MLT_TTS.sample_rate)


In [15]:
ls

 bangla_seerah/
 bangla_tts/
'E2E-Multilingual Speech to Speech Translator.ipynb'
 E2E_Single_Sample_Demo_of_Multilingual_Speech_to_Speech_Translation.ipynb
 e2e_single_sample_demo_of_multilingual_speech_to_speech_translation.py
 empty.wav
 klaam/
 LICENSE
 model.pth.tar
 __pycache__/
 README.md
 sample.wav
 step1_make_youtube_audio_playlist.py
 step2_run_multilingual_stt.py
 step3_crosslingual_translator.py
 step4_multilingual_tts.py
 yasir_qadhi_seerah/
 youtube-playlist-downloader.ipynb
